In [49]:
import pandas as pd
import plotly.express as ex
import plotly.graph_objects as go
import matplotlib.pyplot as plt

In [50]:
data = pd.read_parquet("energy.parquet")
objs = data.columns[-10:]
decs = data.columns[:-10]

short_names = {
    'Yearly total costs': "Costs",
    'Yearly CO2 emissions': "CO2",
    'Resilience': "Res",
    'Mean battery state of charge': "bSOC",
    'Yearly energy discharged from battery': "bDis",
    'Maximum power peak': "Ppeak",
    'SOC Time proportion': "bSOC% Time",
    'Yearly energy fed into the grid': "bGrid",
    'Maximum feed-in power peak': "mPpeak",
    'posResilience': "pRes",
}

data = data.rename(columns=short_names)
objs = [short_names[o] for o in objs]
objs.remove("Res")  # There's alread a posResilience column

In [72]:
data

Photovoltaics.alphaModule  Photovoltaics.betaModule  \
0                       0.510881                  0.975289   
1                       0.122803                  0.309735   
2                       0.121460                  0.744609   
3                       0.089940                  0.054477   
4                       0.394887                  0.912612   
...                          ...                       ...   
20694                   0.711137                  0.891922   
20695                   0.725314                  0.224194   
20696                   0.646708                  0.905856   
20697                   0.784808                  0.392342   
20698                   0.795363                  0.522876   

       Photovoltaics.PPeak  BatteryStorage.EBattNominal  \
0                 0.492850                     0.466698   
1                 0.188685                     0.829031   
2                 0.050332                     0.583919   
3                 0.450046                     0.434629   
4                 0.478879                     0.230624   
...                    ...                          ...   
20694             0.957539                     0.533758   
20695             0.460771                     0.785019   
20696             0.884127                     0.656093   
20697             0.408463                     0.450229   
20698             0.008491                     0.519479   

       BatteryStorage.SOCMax  BatteryStorage.SOCMin  \
0                   0.993841               0.164105   
1                   0.409357               0.277229   
2                   0.981642               0.363049   
3                   0.247517               0.458440   
4                   0.983081               0.326405   
...                      ...                    ...   
20694               0.183120               0.786685   
20695               0.093083               0.682785   
20696               0.040635               0.914418   
20697               0.430142               0.600571   
20698               0.420189               0.922607   

       batteryControllerDT1.lowerLimit  batteryControllerDT1.upperLimit  \
0                             0.037514                         0.102789   
1                             0.803160                         0.435728   
2                             0.798786                         0.771516   
3                             0.094274                         0.339589   
4                             0.821689                         0.659273   
...                                ...                              ...   
20694                         0.999892                         0.685766   
20695                         0.564713                         0.524262   
20696                         0.845369                         0.759375   
20697                         0.991794                         0.226087   
20698                         0.958249                         0.532476   

       HeatingAndCooling.HeatGeneration.HeatStorage.VStorage  \
0                                               0.015456       
1                                               0.823524       
2                                               0.821965       
3                                               0.177055       
4                                               0.454571       
...                                                  ...       
20694                                           0.706252       
20695                                           0.097476       
20696                                           0.966675       
20697                                           0.837512       
20698                                           0.839340       

       Investment costs  ...          CO2          Res      bSOC  \
0         349560.480800  ...  2133.718310 -1014.156523  0.143132   
1         344858.684600  ...  2154.638216  -526.491351  0.103973   
2         286305.7

In [51]:
from desdeo.tools.score_bands import order_objectives, cluster, calculate_axes_positions, SCORE_bands

In [70]:
corr, obj_order = order_objectives(data[objs], use_absolute_corr=False)

# Cluster into 8 groups
obj_to_cluster = "CO2"
n_clusters = 8

data["cluster"] = 1
for i in range(1, n_clusters):
    data.loc[data[obj_to_cluster] > data[obj_to_cluster].quantile(i / n_clusters), "cluster"] = i+1

ordered_data, axis_dist, axis_signs = calculate_axes_positions(
        data[objs],
        obj_order,
        corr,
        dist_parameter=0.521,
        distance_formula=1,
    )

scales = pd.DataFrame([ordered_data.min(axis=0), ordered_data.max(axis=0)], index=["min", "max"])

fig = SCORE_bands(
    ordered_data,
    color_groups=data["cluster"].tolist(),
    bands=True,
    quantile=0.05,
    axis_positions=axis_dist,
    solutions=False,
    scales=scales[ordered_data.columns],
)

fig.update_layout(
    width=1500,
    height=700,
)


In [71]:
# Try making violin for mPpeak, cluster 1

colours = plt.get_cmap("Accent", n_clusters)


for cluster_id in range(1, n_clusters + 1):

    show_legend = True
    for i, current_obj in enumerate(ordered_data.columns):
        current_data = ordered_data.loc[data["cluster"] == cluster_id, current_obj] 
        current_data = current_data - scales.loc["min", current_obj]
        current_data = current_data / (scales.loc["max", current_obj] - scales.loc["min", current_obj])

        r, g, b, a = colours(cluster_id - 1)
        color_violins = f"rgba({r}, {g}, {b}, {a})"
        fig.add_trace(
            go.Violin(
                y=current_data,
                x= [axis_dist[i]] * len(current_data),
                legendgroup=str(cluster_id),
                name=f"Violins for Cluster {cluster_id}" if show_legend else f"Violins for Cluster {cluster_id} {current_obj}",
                #name=f"Cluster {cluster_id}",
                showlegend=show_legend,
                fillcolor=color_violins,
                line_color="black",
            )
        )
        show_legend = False
fig

In [56]:

colours(0)

(np.float64(0.12156862745098039),
 np.float64(0.4666666666666667),
 np.float64(0.7058823529411765),
 np.float64(1.0))